In [1]:
import pandas as pd
#df = pd.read_csv("BTCUSD_Candlestick_1_D_ASK_08.05.2017-18.11.2021.csv")
#df = pd.read_csv("LTCUSD_Candlestick_1_D_ASK_03.09.2018-18.11.2021.csv")
#df = pd.read_csv("ETHUSD_Candlestick_1_D_ASK_12.12.2017-18.11.2021.csv")
#df = pd.read_csv("EURUSD_Candlestick_1_D_ASK_05.05.2003-30.06.2021.csv")
df = pd.read_csv("EURUSD_Candlestick_4_Hour_ASK_05.05.2003-16.10.2021.csv")
#df = pd.read_csv("USDCHF_Candlestick_4_Hour_ASK_05.05.2003-19.10.2019.csv")
#df = df.drop(columns=['Gmt time'])
df=df[df['Volume']!=0]
df.isna().sum()
df.reset_index(drop=True, inplace=True)

In [2]:
df

Gmt time     Open     High      Low    Close  \
0      04.05.2003 21:00:00.000  1.12354  1.12354  1.12166  1.12274   
1      05.05.2003 01:00:00.000  1.12242  1.12276  1.12067  1.12126   
2      05.05.2003 05:00:00.000  1.12139  1.12255  1.12030  1.12113   
3      05.05.2003 09:00:00.000  1.12092  1.12331  1.12049  1.12174   
4      05.05.2003 13:00:00.000  1.12194  1.12900  1.12130  1.12712   
...                        ...      ...      ...      ...      ...   
28821  15.10.2021 01:00:00.000  1.15940  1.16120  1.15938  1.16082   
28822  15.10.2021 05:00:00.000  1.16082  1.16189  1.15995  1.16034   
28823  15.10.2021 09:00:00.000  1.16033  1.16124  1.15892  1.15923   
28824  15.10.2021 13:00:00.000  1.15923  1.16103  1.15893  1.15953   
28825  15.10.2021 17:00:00.000  1.15952  1.16060  1.15933  1.16040   

            Volume  
0       95533.0976  
1       93778.5996  
2       90924.6992  
3       91254.6992  
4      308003.4083  
...            ...  
28821    5738.6300  
28822   13149.6600  
28823   14914.3300  
28824   20002.5300  
28825    5620.0500  

[28826 rows x 6 columns]

In [3]:
import pandas_ta as pa
df["EMA"] = pa.ema(df.Close, length=100)
df['ATR'] = pa.atr(high=df.High, low=df.Low, close=df.Close, length=14)
df[1300:1305]

Gmt time     Open     High      Low    Close  \
1300  02.03.2004 14:00:00.000  1.23942  1.24129  1.21944  1.22061   
1301  02.03.2004 18:00:00.000  1.22097  1.22319  1.22034  1.22152   
1302  02.03.2004 22:00:00.000  1.22137  1.22220  1.21650  1.22003   
1303  03.03.2004 02:00:00.000  1.21992  1.22017  1.21481  1.21783   
1304  03.03.2004 06:00:00.000  1.21781  1.22131  1.21633  1.21635   

           Volume       EMA       ATR  
1300  406237.6954  1.257532  0.006423  
1301  291095.1035  1.256819  0.006168  
1302  109763.5996  1.256090  0.006135  
1303  108383.9980  1.255333  0.006079  
1304  105503.5000  1.254561  0.006001

In [4]:
def EMASig(df1, l, backcandles):
    sigup=2
    sigdn=1
    for i in range(l-backcandles, l+1):
        if df1.Low[i]<=df1.EMA[i]:
            sigup = 0
        if df1.High[i]>=df1.EMA[i]:
            sigdn = 0
    if sigup:
        return sigup
    elif sigdn:
        return sigdn
    else:
        return 0
        
EMASig(df, 409, 7)

0

In [5]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime
dfpl = df[100:1000]
fig = go.Figure(data=[go.Candlestick(x=dfpl.index,
                open=dfpl['Open'],
                high=dfpl['High'],
                low=dfpl['Low'],
                close=dfpl['Close']),
                go.Scatter(x=dfpl.index, y=dfpl.EMA, line=dict(color='orange', width=1), name="EMA")])
fig.show()

In [6]:
#!!!!!!!
EMABackCandles = 30

EMASignal = [0] * len(df)
for row in range(EMABackCandles, len(df)):
    EMASignal[row] = EMASig(df, row, EMABackCandles)

df['EMASignal']=EMASignal


In [9]:
df[100:150]

Gmt time     Open     High      Low    Close       Volume  \
100  27.05.2003 13:00:00.000  1.18944  1.19300  1.18494  1.18534  308324.4980   
101  27.05.2003 17:00:00.000  1.18527  1.18760  1.18249  1.18288  375595.5000   
102  27.05.2003 21:00:00.000  1.18261  1.18290  1.18086  1.18116   95058.2012   
103  28.05.2003 01:00:00.000  1.18155  1.18422  1.18116  1.18322   94809.0996   
104  28.05.2003 05:00:00.000  1.18350  1.18453  1.17619  1.17695   91838.0996   
105  28.05.2003 09:00:00.000  1.17702  1.17977  1.17047  1.17200   90089.0000   
106  28.05.2003 13:00:00.000  1.17207  1.17765  1.17099  1.17427  314511.7950   
107  28.05.2003 17:00:00.000  1.17404  1.17810  1.17209  1.17649  373941.4960   
108  28.05.2003 21:00:00.000  1.17657  1.17703  1.17408  1.17540   93069.0996   
109  29.05.2003 01:00:00.000  1.17548  1.17698  1.17320  1.17423   93883.8008   
110  29.05.2003 05:00:00.000  1.17424  1.17695  1.17024  1.17036   89701.1992   
111  29.05.2003 09:00:00.000  1.17067  1.17774  1.16917  1.17606   91591.9004   
112  29.05.2003 13:00:00.000  1.17634  1.18458  1.17407  1.18250  307693.9023   
113  29.05.2003 17:00:00.000  1.18340  1.19008  1.18271  1.18833  369965.0977   
114  29.05.2003 21:00:00.000  1.18827  1.19158  1.18796  1.18828   94757.6992   
115  30.05.2003 01:00:00.000  1.18804  1.18950  1.18674  1.18734   95444.9980   
116  30.05.2003 05:00:00.000  1.18751  1.18927  1.18433  1.18536   89643.8984   
117  30.05.2003 09:00:00.000  1.18478  1.18556  1.18154  1.18272   91470.5976   
118  30.05.2003 13:00:00.000  1.18243  1.18342  1.17439  1.17620  312367.1992   
119  30.05.2003 17:00:00.000  1.17632  1.17932  1.17558  1.17691  373578.8984   
120  01.06.2003 21:00:00.000  1.17149  1.17476  1.17073  1.17229   96344.5000   
121  02.06.2003 01:00:00.000  1.17220  1.17300  1.16524  1.16748   94696.5000   
122  02.06.2003 05:00:00.000  1.16764  1.17545  1.16649  1.16841   87726.3008   
123  02.06.2003 09:00:00.000  1.16876  1.17196  1.16658  1.16758   92470.5000   
124  02.06.2003 13:00:00.000  1.16735  1.17463  1.16592  1.17402  309753.0977   
125  02.06.2003 17:00:00.000  1.17420  1.17672  1.17394  1.17473  284527.4024   
126  02.06.2003 21:00:00.000  1.17496  1.17686  1.17354  1.17418   92399.4004   
127  03.06.2003 01:00:00.000  1.17397  1.17617  1.17250  1.17552   94262.1016   
128  03.06.2003 05:00:00.000  1.17561  1.17783  1.17428  1.17714   90317.7988   
129  03.06.2003 09:00:00.000  1.17685  1.17751  1.17110  1.17250   90283.0996   
130  03.06.2003 13:00:00.000  1.17228  1.17491  1.16875  1.16998  313103.0977   
131  03.06.2003 17:00:00.000  1.17010  1.17551  1.16976  1.17391  371493.1055   
132  03.06.2003 21:00:00.000  1.17365  1.17449  1.17173  1.17232   92443.8008   
133  04.06.2003 01:00:00.000  1.17235  1.17371  1.17116  1.17247   97601.1992   
134  04.06.2003 05:00:00.000  1.17284  1.17473  1.17082  1.17373   90039.9004   
135  04.06.2003 09:00:00.000  1.17343  1.17426  1.16904  1.17039   89027.1992   
136  04.06.2003 13:00:00.000  1.17032  1.17261  1.16696  1.17053  312423.5039   
137  04.06.2003 17:00:00.000  1.17063  1.17125  1.16619  1.16645  379512.9064   
138  04.06.2003 21:00:00.000  1.16635  1.16639  1.16325  1.16468   92719.2012   
139  05.06.2003 01:00:00.000  1.16460  1.16602  1.16287  1.16531   94807.9004   
140  05.06.2003 05:00:00.000  1.16571  1.16748  1.16428  1.16646   87774.7012   
141  05.06.2003 09:00:00.000  1.16640  1.17398  1.16582  1.17341   91357.4004   
142  05.06.2003 13:00:00.000  1.17417  1.18860  1.17335  1.18692  309839.1992   
143  05.06.2003 17:00:00.000  1.18658  1.18771  1.18327  1.18405  375063.1015   
144  05.06.2003 21:00:00.000  1.18389  1.18531  1.18313  1.18342   95687.0000   
145  06.06.2003 01:00:00.000  1.18341  1.18576  1.18295  1.18484   99047.9004   
146  06.06.2003 05:00:00.000  1.18487  1.18579  1.18179  1.18319   87714.7988   
147  06.06.2003 09:00:00.000  1.18336  1.18785  1.18168  1.18172   90740.2988   
148  06.06.2003 13:00:00.000  1.18136  1.18205  1.1

In [7]:
df.dropna(inplace=True)
df.reset_index(drop=True, inplace=True)

In [8]:
HLBackCandles = 8

df['mins'] = df['Low'].rolling(window=HLBackCandles).min()
df['maxs'] = df['High'].rolling(window=HLBackCandles).max()

def HLSig(x):
    if x.EMASignal == 1 and x.High>=x.maxs:
        return 1
    if x.EMASignal == 2 and x.Low<=x.mins:
        return 2
    else:
        return 0
    
df["HLSignal"] = df.apply(HLSig, axis=1)

df[df['HLSignal']==1]

Gmt time     Open     High      Low    Close  \
145    30.06.2003 13:00:00.000  1.14278  1.15018  1.14209  1.14994   
146    30.06.2003 17:00:00.000  1.15014  1.15141  1.14719  1.15116   
147    30.06.2003 21:00:00.000  1.15154  1.15336  1.15025  1.15185   
148    01.07.2003 01:00:00.000  1.15214  1.15408  1.15094  1.15136   
149    01.07.2003 05:00:00.000  1.15142  1.15493  1.15056  1.15370   
...                        ...      ...      ...      ...      ...   
28699  11.10.2021 05:00:00.000  1.15725  1.15869  1.15644  1.15700   
28713  13.10.2021 13:00:00.000  1.15430  1.15788  1.15405  1.15780   
28714  13.10.2021 17:00:00.000  1.15781  1.15975  1.15780  1.15956   
28715  13.10.2021 21:00:00.000  1.15961  1.16013  1.15925  1.15992   
28717  14.10.2021 05:00:00.000  1.15900  1.16191  1.15880  1.16166   

            Volume       EMA       ATR  EMASignal     mins     maxs  HLSignal  
145    308576.4063  1.160490  0.004540          1  1.13974  1.15018         1  
146    373270.7030  1.160305  0.004517          1  1.13974  1.15141         1  
147     93724.5996  1.160138  0.004416          1  1.13974  1.15336         1  
148     96315.0000  1.159964  0.004325          1  1.13974  1.15408         1  
149     93260.7012  1.159840  0.004328          1  1.13974  1.15493         1  
...            ...       ...       ...        ...      ...      ...       ...  
28699   13671.1800  1.164416  0.001859          1  1.15416  1.15869         1  
28713   23598.1900  1.162148  0.002018          1  1.15244  1.15788         1  
28714   11188.6800  1.162097  0.002013          1  1.15244  1.15975         1  
28715    4511.0400  1.162053  0.001933          1  1.15244  1.16013         1  
28717   20309.8200  1.161986  0.001967          1  1.15363  1.16191         1  

[881 rows x 12 columns]

In [9]:
import numpy as np
def pointpos(x):
    if x['HLSignal']==1:
        return x['High']+1e-3
    elif x['HLSignal']==2:
        return x['Low']-1e-3
    else:
        return np.nan

df['pointpos'] = df.apply(lambda row: pointpos(row), axis=1)

In [10]:
dfpl = df[100:250]
fig = go.Figure(data=[go.Candlestick(x=dfpl.index,
                open=dfpl['Open'],
                high=dfpl['High'],
                low=dfpl['Low'],
                close=dfpl['Close']),
                go.Scatter(x=dfpl.index, y=dfpl.EMA, line=dict(color='orange', width=1), name="EMA")])

fig.add_scatter(x=dfpl.index, y=dfpl['pointpos'], mode="markers",
                marker=dict(size=5, color="MediumPurple"),
                name="Signal")
fig.show()

In [34]:
def SIGNAL():
    return df.HLSignal

In [43]:
#ATR distance Trailing SL
from backtesting import Strategy, Backtest
import numpy as np

class MyStrat(Strategy):
    atr_f = 1
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        for trade in self.trades: 
            if trade.is_long: 
                trade.sl = max(trade.sl or -np.inf, self.data.Close[-1] - self.data.ATR[-1]/self.atr_f)
            else:
                trade.sl = min(trade.sl or np.inf, self.data.Close[-1] + self.data.ATR[-1]/self.atr_f)

        if self.signal1==2 and len(self.trades)<=0: # trades number change!
            sl1 = self.data.Close[-1] - self.data.ATR[-1]/self.atr_f
            self.buy(sl=sl1)
        elif self.signal1==1 and len(self.trades)<=0: # trades number change!
            sl1 = self.data.Close[-1] + self.data.ATR[-1]/self.atr_f
            self.sell(sl=sl1)

bt = Backtest(df, MyStrat, cash=10_000, commission=.000)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                    1357.0
Duration                               1357.0
Exposure Time [%]                    9.572901
Equity Final [$]                 10090.917743
Equity Peak [$]                    10283.1987
Return [%]                           0.909177
Buy & Hold Return [%]               -0.743361
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                  -11.079205
Avg. Drawdown [%]                   -2.924363
Max. Drawdown Duration                 1176.0
Avg. Drawdown Duration                 296.25
# Trades                                 32.0
Win Rate [%]                           28.125
Best Trade [%]                       3.582501
Worst Trade [%]                      -2.82096
Avg. Trade [%]                    

In [23]:
bt.plot()

Row(id='1456', ...)

In [45]:
# ATR fixed SL and TP
from backtesting import Strategy, Backtest

class MyStrat(Strategy):
    atr_f = 1.
    SLTPR = 1.5
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next() 
        if self.signal1==2:
            #sl1 = self.data.Close[-1] - 750e-4 #EURUSD
            #tp1 = self.data.Close[-1] + 600e-4
            #sl1 = self.data.Close[-1] - 30 #ETHUSD
            #tp1 = self.data.Close[-1] + 40
            sl1 = self.data.Close[-1] - self.data.ATR[-1]/self.atr_f #USDCHF
            tp1 = self.data.Close[-1] + self.data.ATR[-1]*self.SLTPR/self.atr_f
            self.buy(sl=sl1, tp=tp1)
        elif self.signal1==1:
            #sl1 = self.data.Close[-1] + 750e-4 #EURUSD
            #tp1 = self.data.Close[-1] - 600e-4
            #sl1 = self.data.Close[-1] + 30 #ETHUSD
            #tp1 = self.data.Close[-1] - 40
            sl1 = self.data.Close[-1] + self.data.ATR[-1]/self.atr_f #USDCHF
            tp1 = self.data.Close[-1] - self.data.ATR[-1]*self.SLTPR/self.atr_f
            self.sell(sl=sl1, tp=tp1)
bt = Backtest(df, MyStrat, cash=10_000, commission=.000)
stat = bt.run()
stat

D:\ProgramFiles\Anaconda3\lib\site-packages\ipykernel_launcher.py:29: UserWarning:

Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.



Start                                     0.0
End                                    1357.0
Duration                               1357.0
Exposure Time [%]                    3.976436
Equity Final [$]                  9849.817064
Equity Peak [$]                  10027.062123
Return [%]                          -1.501829
Buy & Hold Return [%]               -0.743361
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              0.0
Max. Drawdown [%]                    -4.86963
Avg. Drawdown [%]                    -1.43031
Max. Drawdown Duration                  583.0
Avg. Drawdown Duration                 233.25
# Trades                                 45.0
Win Rate [%]                        11.111111
Best Trade [%]                       2.059105
Worst Trade [%]                     -2.448162
Avg. Trade [%]                    